# Simple Notebook for Visualizing Accelerometer Data  of 10 Steps

In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import sys
sys.path.append('../')
from Code.helpers import butter_lowpass_filter, helper_find_peaks, normalize

## Read the Data

In [2]:
df_acc = pd.read_csv('../Data/Data_Nils/MDS_Scenario_2_nils_1 2022-05-23 10-48-47/Accelerometer.csv')
readings_np = df_acc.to_numpy()
readings_np.shape

(11349, 4)

## Normalize Data

In [3]:
norm_readings_np = np.apply_along_axis(normalize, 1, readings_np[:, 1:])

### Filter All Readings Besides the Time

In [4]:
filtered_readings_np = np.apply_along_axis(butter_lowpass_filter, 0, norm_readings_np)

In [5]:
filtered_readings_np = np.c_[readings_np[:, 0], filtered_readings_np]

## Plot the Filtered Data

In [6]:
# Filter the data, and plot both the original and filtered signals.
fig = go.Figure()

fig.add_trace(go.Scatter(
            x = filtered_readings_np[:, 0],
            y = filtered_readings_np[:, 1],
            line =  dict(shape =  'spline' ),
            name = 'normailzed signal')
            )


fig.show()

## Push Mean of Data to 0

In [7]:
pushed_filtered_readings_np = filtered_readings_np - filtered_readings_np.mean(axis=0, keepdims=True)

## Find the peaks

In [8]:
# find peaks in absolute acceleration -> resulting in steps
columns = ["norm"]

peaks = helper_find_peaks(pushed_filtered_readings_np[:, 1])


print('Number of peaks in data', columns, ':', len(peaks))

Number of peaks in data ['norm'] : 71


## Show Peaks In Z-Axis

In [9]:
pushed_filtered_df = pd.DataFrame(pushed_filtered_readings_np, columns=['time', 'norm'])

In [10]:
fig = go.Figure()

fig.add_trace(go.Scatter(
            y = pushed_filtered_df['norm'],
            line =  dict(shape =  'spline' ),
            name = 'signal')
            )
fig.add_trace(go.Scatter(
            x = peaks,
            y = pushed_filtered_df.loc[peaks]['norm'],
            mode =  'markers',
            name = 'peaks')
            )
